In [1]:
import arkouda as ak
import arachne as ar
import scipy as sp
import networkx as nx
import matplotlib.pyplot as plt
import os
from pathlib import Path
import pandas as pd
import numpy as np
import navis
from fafbseg import flywire
from compcon.navis_api import get_flywire_neuron, get_hemibrain_neuron
from compcon.create_graph import get_neuron, get_graph, draw_graph, get_neuron_local, overall, draw_connection, draw3d_graph
from compcon.isomporphic_subgraphs import find_isomorphic_subgraphs
import itertools
from skelescope.skelescope import Skelescope
from vimosketches.src.anywidget_test import Widget
import random

    _         _                   _       
   / \   _ __| | _____  _   _  __| | __ _ 
  / _ \ | '__| |/ / _ \| | | |/ _` |/ _` |
 / ___ \| |  |   < (_) | |_| | (_| | (_| |
/_/   \_\_|  |_|\_\___/ \__,_|\__,_|\__,_|
                                          

Client Version: v2024.04.19


In [2]:
# Load the CSV file into a DataFrame
df = pd.read_csv('column_assignment.csv')

# Extract root_id and column_id
df = df[['root_id', 'column_id']]
ids=[]
for i in range(2):
    ids.extend(df[df["column_id"] == (i+1)]["root_id"].values.tolist())

In [3]:
nd0 = get_neuron_local(ids[0], 3000)
nd0.nodes
# nd0.nodes["x"].values.tolist()

node_id label            x              y              z  radius  type  \
0           1     1  739292.2500  205695.343750   82705.820312  2038.0  root   
1           5     0  739352.3125  205748.375000   82859.492188  2093.0  slab   
2           6     0  738998.5000  204439.125000   98680.250000   217.0  slab   
3           7     0  739030.3750  204581.656250   98705.789062   210.0  slab   
4           8     0  738967.0000  204254.046875   98648.804688   215.0  slab   
...       ...   ...          ...            ...            ...     ...   ...   
1292     2075     0  767384.9375  219429.593750  110954.976562   277.0  slab   
1293     2076     0  767656.5625  218847.937500  110570.023438   405.0  slab   
1294     2077     0  767612.8750  218916.968750  110694.632812   376.0  slab   
1295     2078     0  767512.1875  219152.531250  110900.828125   270.0  slab   
1296     2079     0  767546.7500  219008.296875  110797.968750   333.0  slab   

      parent_id  
0            -1  
1             1  
2             8  
3             6  
4            10  
...         ...  
1292       2078  
1293       2074  
1294       2076  
1295       2079  
1296       2077  

[1297 rows x 8 columns]

In [4]:
# Load the CSV file
classification = pd.read_csv('classification.csv')

# Filter for 'optic' in 'super_class' and 'right' in 'side'
filtered_classification = classification[(classification['super_class'] == 'optic') & (classification['side'] == 'right')]

# Display the filtered DataFrame
# print(filtered_df)

# Get the 'root_id' for the filtered rows
root_ids = filtered_classification['root_id'].tolist()

# print("Filtered root IDs:")
# print(root_ids)


In [5]:
# Load the CSV file
classification = pd.read_csv('visual_neuron_types.csv')

# Filter for 'optic' in 'super_class' and 'right' in 'side'
filtered_visn = classification[(classification['category'] == 'OL intrinsic') & 
((classification['family'] == 'Medulla Intrinsic') | (classification['family'] == 'T4 Neuron') | 
 (classification['family'] == 'Lamina Intrinsic') | (classification['family'] == 'Lobula Intrinsic') | (classification['family'] == 'Centrifugal') | 
 (classification['family'] == 'Distal Medulla'))]

# Display the filtered DataFrame
# print(filtered_df)

# Get the 'root_id' for the filtered rows
root_ids2 = filtered_visn['root_id'].tolist()
len(root_ids2)
# root_ids2 = classification['root_id'].tolist()

# print("Filtered root IDs:")
# print(root_ids)


12813

In [6]:
syn_co = pd.read_csv('synapse_coordinates.csv', dtype={'pre_root_id': str, 'post_root_id': str})

# Forward fill the empty values
syn_co['pre_root_id'].ffill(inplace=True)
syn_co['post_root_id'].ffill(inplace=True)

# Convert the columns to int64 now that the missing values are filled
syn_co['pre_root_id'] = syn_co['pre_root_id'].astype('int64')
syn_co['post_root_id'] = syn_co['post_root_id'].astype('int64')
# filtered_df = syn_co[syn_co['pre_root_id'].isin(root_ids) & syn_co['post_root_id'].isin(root_ids)]
# combos = filtered_df[['pre_root_id', 'post_root_id']].drop_duplicates().values.tolist()

ParserError: Error tokenizing data. C error: Calling read(nbytes) on source failed. Try engine='python'.

In [ ]:
# Assuming root_ids is your list of IDs
filtered_df = syn_co[syn_co['pre_root_id'].isin(root_ids2) & syn_co['post_root_id'].isin(root_ids2)]

In [ ]:
syn_co[syn_co['pre_root_id'].isin(root_ids2[400:900]) & syn_co['post_root_id'].isin(root_ids2[400:900])]

In [10]:
# filtered_df[(filtered_df['pre_root_id'] == syn_ids[0]) | (filtered_df['post_root_id'] == syn_ids[0])]

In [11]:
pre = filtered_df['pre_root_id'].drop_duplicates().values.tolist()
post = filtered_df['post_root_id'].drop_duplicates().values.tolist()
syn_ids = list(set(pre + post))
print(len(syn_ids), len(pre+post))
gloabl_mapping = {}
for idd in syn_ids:
    # Create a consistent random multiplier based on the neuron ID
    random.seed(idd)
    consistent_multiplier = random.randint(1, 1000000000000)
    x_temp=[]
    y_temp=[]
    z_temp=[]
    print((syn_ids.index(idd)/len(syn_ids))*100, "%")
    filtered_dff = filtered_df[(filtered_df['pre_root_id'] == idd) | (filtered_df['post_root_id'] == idd)]
    # print(list(set(filtered_dff['pre_root_id'].tolist())))
    # print(list(set(filtered_dff['post_root_id'].tolist())))
    indexes = filtered_dff.index.tolist()
    
    nd00 = get_neuron_local(idd, 3000)
    
    x_temp.extend(filtered_dff.loc[:, "x"])
    y_temp.extend(filtered_dff.loc[:, "y"])
    z_temp.extend(filtered_dff.loc[:, "z"])

    c_coordinates = np.vstack((x_temp, y_temp, z_temp)).T

    idloc1, dist1 = nd00.snap(c_coordinates)

    
    nd0 = navis.downsample_neuron(nd00, downsampling_factor=10000, inplace=False)

    np0 = navis.downsample_neuron(nd00, downsampling_factor=10000, preserve_nodes=idloc1, inplace=False)

    map0 = []
    map1 = []
    nd0_array = np.array(nd0.edges)
    map0 = map0 + list(nd0_array[:,0])
    map1 = map1 + list(nd0_array[:,0]*consistent_multiplier + nd0_array[:,1])

    map0 = map0 + list(nd0_array[:,1])
    map1 = map1 + list(nd0_array[:,0]*consistent_multiplier + nd0_array[:,1])

    nd0edges=nd0.edges
    nd0 = set(map(tuple, nd0.edges))
    np0 = set(map(tuple, np0.edges))
    
    # Find the difference
    difference_set1 = nd0 - np0
    difference_set2 = np0 - nd0

    difference_set1 = list(map(list, difference_set1))
    difference_set2 = list(map(list, difference_set2))
    print("nd0:", len(nd0edges), len(difference_set1), len(difference_set2))

    nx_display = nx.Graph()
    nx_display.add_edges_from(difference_set2)
    
    for eds in difference_set1:
        start_node_id = eds[0]
        end_node_id = eds[1]
        
        shortest_path = nx.shortest_path(nx_display, source=start_node_id, target=end_node_id, weight='weight')

        if len(shortest_path) > 2:
            inner_path = shortest_path[1:-1]
            map0.extend(inner_path)
            map1.extend(len(inner_path)*[eds[0]*consistent_multiplier+eds[1]])

    
    mapping0 = dict(zip(map0, map1))
    idloc1 = np.vectorize(mapping0.get)(idloc1).tolist()

    index_to_id_mapping = dict(zip(indexes, idloc1))
    gloabl_mapping[idd] = index_to_id_mapping
    # filtered_df.loc[dff.index.tolist()]


12164 19448
0.0 %
nd0: 170 23 62
0.008220979940808944 %
nd0: 72 43 169
0.01644195988161789 %
nd0: 35 16 86
0.024662939822426833 %
nd0: 50 29 111
0.03288391976323578 %
nd0: 52 4 9
0.041104899704044726 %
nd0: 25 1 3
0.04932587964485367 %
nd0: 31 7 22
0.05754685958566261 %
nd0: 29 3 11
0.06576783952647156 %
nd0: 60 37 143
0.0739888194672805 %
nd0: 29 12 38
0.08220979940808945 %
nd0: 221 81 204
0.09043077934889839 %
nd0: 19 8 26
0.09865175928970733 %
nd0: 34 14 81
0.10687273923051628 %
nd0: 32 12 34
0.11509371917132522 %
nd0: 19 4 13
0.12331469911213418 %
nd0: 164 60 143
0.1315356790529431 %
nd0: 48 21 109
0.13975665899375206 %
nd0: 67 2 6
0.147977638934561 %
nd0: 45 14 43
0.15619861887536995 %
nd0: 49 19 90
0.1644195988161789 %
nd0: 37 8 23
0.17264057875698782 %
nd0: 27 14 88
0.18086155869779677 %
nd0: 27 8 20
0.18908253863860575 %
nd0: 29 6 26
0.19730351857941467 %
nd0: 21 4 13
0.20552449852022361 %
nd0: 220 23 55
0.21374547846103256 %
nd0: 48 14 39
0.22196645840184148 %
nd0: 42 4 10
0.2

In [12]:
safee = gloabl_mapping

In [13]:
combos = filtered_df[['pre_root_id', 'post_root_id']].drop_duplicates().values.tolist()

In [14]:
# def snap_coordinates(src, dst, s_x, s_y, s_z, s_x_t, s_y_t, s_z_t, d_x, d_y, d_z, d_x_t, d_y_t, d_z_t, c_coordinates):
#     src_2 = np.array(src) + 1000
#     src_2 = list(src_2)

#     src_3 = np.array(src) + 1000000
#     src_3 = list(src_3)

#     dst_2 = np.array(dst) + 1000
#     dst_2 = list(dst_2)

#     dst_3 = np.array(dst) + 1000000
#     dst_3 = list(dst_3)
    
#     # Create unique IDs for each src and dst element
#     unique_src_ids = list(range(1000, 1000 + len(s_x_t)))  # Example range for unique IDs for src
#     unique_dst_ids = list(range(2000, 2000 + len(d_x_t)))  # Example range for unique IDs for dst


#     # syn_mapping = dict(zip(src + src_2 + src_3 + dst + dst_2 + dst_3, src + src + src + dst + dst + dst))
#     syn_mapping = dict(zip(unique_src_ids  + unique_dst_ids, src + src + src + src + src + src + src + src + src + dst + dst + dst + dst + dst + dst + dst + dst + dst))
    
#     # data = {
#     #     'x': s_x + s_x_2 + s_x_3 + d_x + d_x_2 + d_x_3,
#     #     'y': s_y + s_y_2 + s_y_3 + d_y + d_y_2 + d_y_3,
#     #     'z': s_z + s_z_2 + s_z_3 + d_z + d_z_2 + d_z_3,
#     #     'node_id': src + src_2 + src_3 + dst + dst_2 + dst_3,
#     #     'parent_id': [0] * len(src + src_2 + src_3 + dst + dst_2 + dst_3)
#     # }
#     data = {
#         'x': s_x_t + d_x_t,
#         'y': s_y_t + d_y_t,
#         'z': s_z_t + d_z_t,
#         'node_id': unique_src_ids  + unique_dst_ids,
#         'parent_id': [0] * len(s_x_t + d_x_t)
#     }
    
#     df = pd.DataFrame(data).copy()

#     new_n = navis.TreeNeuron(
#         df[['node_id', 'parent_id', 'x', 'y', 'z']],
#         None
#     )

#     n_ids, dists = new_n.snap(c_coordinates)
#     n_ids = list(n_ids)

#     syn_ids = np.vectorize(syn_mapping.get)(n_ids)

#     return syn_ids, dists



In [15]:
# def synaptic_data1(neurons, id_list):
#     synaptic_src, synaptic_s_bef, synaptic_s_af, synaptic_d_bef, synaptic_d_af, synaptic_dst, x, y, z, n_combo, dists = [], [], [], [], [], [], [], [], [], [], []
#     # # combinations = list(itertools.combinations(id_list, 2))
#     # syn_co = pd.read_csv('synapse_coordinates.csv', dtype={'pre_root_id': str, 'post_root_id': str})

#     # # Forward fill the empty values
#     # syn_co['pre_root_id'].ffill(inplace=True)
#     # syn_co['post_root_id'].ffill(inplace=True)
    
#     # # Convert the columns to int64 now that the missing values are filled
#     # syn_co['pre_root_id'] = syn_co['pre_root_id'].astype('int64')
#     # syn_co['post_root_id'] = syn_co['post_root_id'].astype('int64')
#     filtered_df = syn_co[syn_co['pre_root_id'].isin(id_list) & syn_co['post_root_id'].isin(id_list)]
#     combinations = filtered_df[['pre_root_id', 'post_root_id']].drop_duplicates().values.tolist()

#     for combo in combinations:
#             comp_dif1, comp_dif2, comp_idloc = [], [], []
#             x_temp, y_temp, z_temp = [], [], []
            
#             df1 = filtered_df[(filtered_df['pre_root_id'] == combo[0]) & (filtered_df['post_root_id'] == combo[1])]

#             # if df1.empty and df2.empty:
#             if df1.empty:
#                 continue
                
#             print(combo, (combinations.index(combo)/len(combinations))*100, "%")
        
#             nd0 = get_neuron_local(combo[0], 3000)
#             nd1 = get_neuron_local(combo[1], 3000)

#             x_temp.extend(df1.loc[:, "x"])
#             y_temp.extend(df1.loc[:, "y"])
#             z_temp.extend(df1.loc[:, "z"])

#             c_coordinates = np.vstack((x_temp, y_temp, z_temp)).T

#             idloc1, dist1 = nd0.snap(c_coordinates)
#             idloc2, dist2 = nd1.snap(c_coordinates)

#             comp_idloc.append(idloc1)
#             comp_idloc.append(idloc2)

#             nd0 = get_neuron_local(combo[0], 3000, 10000)
#             nd1 = get_neuron_local(combo[1], 3000, 10000)
        
#             np0 = get_neuron_local(combo[0], 3000, 10000, idloc1)
#             np1 = get_neuron_local(combo[1], 3000, 10000, idloc2)
        

#             map0 = []
#             map1 = []
#             nd0_array = np.array(nd0.edges)
#             map0 = map0 + list(nd0_array[:,0])
#             map1 = map1 + list(nd0_array[:,0]*10000 + nd0_array[:,1])
        
#             map0 = map0 + list(nd0_array[:,1])
#             map1 = map1 + list(nd0_array[:,0]*10000 + nd0_array[:,1])
#             nd0edges=nd0.edges
#             nd0 = set(map(tuple, nd0.edges))
#             np0 = set(map(tuple, np0.edges))
            
#             # Find the difference
#             difference_set1 = nd0 - np0
#             difference_set2 = np0 - nd0
        
#             difference_set1 = list(map(list, difference_set1))
#             difference_set2 = list(map(list, difference_set2))
#             print("nd0:", len(nd0edges), len(difference_set1))
#             comp_dif1.append(difference_set1)
#             comp_dif2.append(difference_set2)
        
#             # nx_display = nx.Graph()
#             # nx_display.add_edges_from(difference_set2)
            
#             # for eds in difference_set1:
#             #     start_node_id = eds[0]
#             #     end_node_id = eds[1]
                
#             #     shortest_path = nx.shortest_path(nx_display, source=start_node_id, target=end_node_id, weight='weight')

#             #     if len(shortest_path) > 2:
#             #         inner_path = shortest_path[1:-1]
#             #         map0.extend(inner_path)
#             #         map1.extend(len(inner_path)*[eds[0]*10000+eds[1]])
                    
#             # mapping0 = dict(zip(map0, map1))
        
#             map0 = []
#             map1 = []
#             nd1_array = np.array(nd1.edges)
#             map0 = map0 + list(nd1_array[:,0])
#             map1 = map1 + list(nd1_array[:,0]*10000 + nd1_array[:,1])
        
#             map0 = map0 + list(nd1_array[:,1])
#             map1 = map1 + list(nd1_array[:,0]*10000 + nd1_array[:,1])
#             nd1edges=nd1.edges
#             nd1 = set(map(tuple, nd1.edges))
#             np1 = set(map(tuple, np1.edges))
            
#             # Find the difference
#             difference_set1 = nd1 - np1
#             difference_set2 = np1 - nd1
        
#             difference_set1 = list(map(list, difference_set1))
#             difference_set2 = list(map(list, difference_set2))
#             print("nd1", len(nd1edges), len(difference_set1))

#             comp_dif1.append(difference_set1)
#             comp_dif2.append(difference_set2)

            
#             for i in range(len(comp_dif1)):
#                 map0, map1 = [], []
#                 nx_display = nx.Graph()
#                 nx_display.add_edges_from(difference_set2[i])
                
#                 for eds in difference_set1[i]:
#                     start_node_id = eds[0]
#                     end_node_id = eds[1]
                    
#                     shortest_path = nx.shortest_path(nx_display, source=start_node_id, target=end_node_id, weight='weight')
    
#                     if len(shortest_path) > 2:
#                         inner_path = shortest_path[1:-1]
#                         map0.extend(inner_path)
#                         map1.extend(len(inner_path)*[eds[0]*10000+eds[1]])
#                 mapping = dict(zip(map0, map1))
#                 #if i even and 0
#                 idloc1.extend(np.vectorize(mapping.get)(comp_idloc[i]).tolist())
#                 #if i uneven
#                 idloc2.extend(np.vectorize(mapping.get)(comp_idloc[i]).tolist())
#             # mapping1 = dict(zip(map0, map1))
                
#             # nx_display = nx.Graph()
#             # nx_display.add_edges_from(difference_set2)
            
#             # for eds in difference_set1:
#             #     start_node_id = eds[0]
#             #     end_node_id = eds[1]
                
#             #     shortest_path = nx.shortest_path(nx_display, source=start_node_id, target=end_node_id, weight='weight')

#             #     if len(shortest_path) > 2:
#             #         inner_path = shortest_path[1:-1]
#             #         map0.extend(inner_path)
#             #         map1.extend(len(inner_path)*[eds[0]*10000+eds[1]])
                    
#             # mapping1 = dict(zip(map0, map1))

#             # idloc1 = np.vectorize(mapping0.get)(idloc1).tolist()
#             # idloc2 = np.vectorize(mapping1.get)(idloc2).tolist()
            
#             # synaptic_s_bef_temp = np.vectorize(neurons[combo[0]]["bef_mapping"].get)(idloc1)
#             # synaptic_s_af_temp = np.vectorize(neurons[combo[0]]["af_mapping"].get)(idloc1)
#             # synaptic_d_bef_temp = np.vectorize(neurons[combo[1]]["bef_mapping"].get)(idloc2)
#             # synaptic_d_af_temp = np.vectorize(neurons[combo[1]]["af_mapping"].get)(idloc2)
#             # # print(synaptic_s_bef_temp)
#             # synaptic_src.extend(idloc1)
#             # synaptic_s_bef.extend(synaptic_s_bef_temp)
#             # synaptic_s_af.extend(synaptic_s_af_temp)
#             # synaptic_dst.extend(idloc2)
#             # synaptic_d_bef.extend(synaptic_d_bef_temp)
#             # synaptic_d_af.extend(synaptic_d_af_temp)
#             # n_combo.extend([(f"{combo[0]}_{combo[1]}")] * len(idloc1))
#             # x.extend(x_temp)
#             # y.extend(y_temp)
#             # z.extend(z_temp)
#             # dists.extend(dist1 + dist2)
            
#     connection_type_s = ["s"] * len(synaptic_src)
    
#     return synaptic_src, synaptic_dst, connection_type_s, x, y, z, n_combo, dists, synaptic_s_bef, synaptic_s_af, synaptic_d_bef, synaptic_d_af

In [16]:
def synaptic_data(neurons, id_list):
    synaptic_src, synaptic_s_bef, synaptic_s_af, synaptic_d_bef, synaptic_d_af, synaptic_dst, x, y, z, n_combo, dists = [], [], [], [], [], [], [], [], [], [], []
    # # combinations = list(itertools.combinations(id_list, 2))
    # syn_co = pd.read_csv('synapse_coordinates.csv', dtype={'pre_root_id': str, 'post_root_id': str})

    # # Forward fill the empty values
    # syn_co['pre_root_id'].ffill(inplace=True)
    # syn_co['post_root_id'].ffill(inplace=True)
    
    # # Convert the columns to int64 now that the missing values are filled
    # syn_co['pre_root_id'] = syn_co['pre_root_id'].astype('int64')
    # syn_co['post_root_id'] = syn_co['post_root_id'].astype('int64')
    filtered_df = syn_co[syn_co['pre_root_id'].isin(id_list) & syn_co['post_root_id'].isin(id_list)]
    combinations = filtered_df[['pre_root_id', 'post_root_id']].drop_duplicates().values.tolist()

    for combo in combinations:
            
            x_temp, y_temp, z_temp = [], [], []
            
            df1 = filtered_df[(filtered_df['pre_root_id'] == combo[0]) & (filtered_df['post_root_id'] == combo[1])]
            
            # if df1.empty and df2.empty:
            if df1.empty:
                continue
                
            print(combo, (combinations.index(combo)/len(combinations))*100, "%")
            indexes = df1.index.tolist()

            x_temp.extend(df1.loc[:, "x"])
            y_temp.extend(df1.loc[:, "y"])
            z_temp.extend(df1.loc[:, "z"])

            mapping0 = gloabl_mapping[combo[0]]
            mapping1 = gloabl_mapping[combo[1]]
            
            idloc1 = np.vectorize(mapping0.get)(indexes).tolist()
            idloc2 = np.vectorize(mapping1.get)(indexes).tolist()
                
            synaptic_s_bef_temp = np.vectorize(lambda x: neurons[combo[0]]["bef_mapping"].get(x, 0))(idloc1)
            synaptic_s_af_temp = np.vectorize(lambda x: neurons[combo[0]]["af_mapping"].get(x, 0))(idloc1)
            synaptic_d_bef_temp = np.vectorize(lambda x: neurons[combo[1]]["bef_mapping"].get(x, 0))(idloc2)
            synaptic_d_af_temp = np.vectorize(lambda x: neurons[combo[1]]["af_mapping"].get(x, 0))(idloc2)
            
            synaptic_src.extend(idloc1)
            synaptic_s_bef.extend(synaptic_s_bef_temp)
            synaptic_s_af.extend(synaptic_s_af_temp)
            synaptic_dst.extend(idloc2)
            synaptic_d_bef.extend(synaptic_d_bef_temp)
            synaptic_d_af.extend(synaptic_d_af_temp)
            n_combo.extend([(f"{combo[0]}_{combo[1]}")] * len(idloc1))
            x.extend(x_temp)
            y.extend(y_temp)
            z.extend(z_temp)
            dists.extend([0]* len(idloc1))
            # dists.extend(dist1 + dist2)
            
    connection_type_s = ["s"] * len(synaptic_src)
    
    return synaptic_src, synaptic_dst, connection_type_s, x, y, z, n_combo, dists, synaptic_s_bef, synaptic_s_af, synaptic_d_bef, synaptic_d_af

In [17]:
def spatial_connectome_creation(edges, n_ds):
    # Create a consistent random multiplier based on the neuron ID
    random.seed(int(n_ds.id))
    consistent_multiplier = random.randint(1, 1000000000000)
    ### create new Graph ### 
    first_elements = edges[:, 0]
    second_elements = edges[:, 1]
    neighbor_matrix = (first_elements[:, np.newaxis] == second_elements[np.newaxis, :])

    # Step 3: Extract neighbor pairs
    neighbor_indices = np.argwhere(neighbor_matrix)
    neighbor_indices = neighbor_indices[neighbor_indices[:, 0] != neighbor_indices[:, 1]]
    neighbor_pairs = edges[neighbor_indices]

    # Step 4: Combine node indices to create unique identifiers for edges
    src_combined = neighbor_pairs[:, 0, 0] * consistent_multiplier + neighbor_pairs[:, 0, 1]
    dst_combined = neighbor_pairs[:, 1, 0] * consistent_multiplier + neighbor_pairs[:, 1, 1]
    
    # Convert to lists for Arkouda
    src = src_combined.astype(np.int64).tolist()
    dst = dst_combined.astype(np.int64).tolist()

    ### get coordinates and calculate distances of nodes ###
    s_bef = neighbor_pairs[:, 0, 0].astype(np.int64).tolist()
    s_af = neighbor_pairs[:, 0, 1].astype(np.int64).tolist()

    d_bef = neighbor_pairs[:, 1, 0].astype(np.int64).tolist()
    d_af = neighbor_pairs[:, 1, 1].astype(np.int64).tolist()

    ###mapping###
    bef_mapping = dict(zip(src + dst, s_bef + d_bef))
    af_mapping = dict(zip(src + dst, s_af + d_af))

    # Create DataFrame for s_bef and s_af with their corresponding coordinates
    s_bef_coords = n_ds.nodes.set_index('node_id').loc[s_bef][['x', 'y', 'z']].reset_index()
    s_af_coords = n_ds.nodes.set_index('node_id').loc[s_af][['x', 'y', 'z']].reset_index()

    d_bef_coords = n_ds.nodes.set_index('node_id').loc[d_bef][['x', 'y', 'z']].reset_index()
    d_af_coords = n_ds.nodes.set_index('node_id').loc[d_af][['x', 'y', 'z']].reset_index()

    # Ensure lengths match by repeating coordinates for each occurrence
    s_bef_coords_repeated = s_bef_coords.loc[s_bef_coords.index.repeat(s_bef_coords.index.value_counts().reindex(s_bef_coords.index).fillna(1))]
    s_af_coords_repeated = s_af_coords.loc[s_af_coords.index.repeat(s_af_coords.index.value_counts().reindex(s_af_coords.index).fillna(1))]

    d_bef_coords_repeated = d_bef_coords.loc[d_bef_coords.index.repeat(d_bef_coords.index.value_counts().reindex(d_bef_coords.index).fillna(1))]
    d_af_coords_repeated = d_af_coords.loc[d_af_coords.index.repeat(d_af_coords.index.value_counts().reindex(d_af_coords.index).fillna(1))]

    # Extract coordinates as numpy arrays
    x_bef, y_bef, z_bef = s_bef_coords_repeated['x'].values, s_bef_coords_repeated['y'].values, s_bef_coords_repeated['z'].values
    x_af, y_af, z_af = s_af_coords_repeated['x'].values, s_af_coords_repeated['y'].values, s_af_coords_repeated['z'].values

    s_bef_x = x_bef.astype(np.int64).tolist()
    s_bef_y = y_bef.astype(np.int64).tolist()
    s_bef_z = z_bef.astype(np.int64).tolist()
    
    s_af_x = x_af.astype(np.int64).tolist()
    s_af_y = y_af.astype(np.int64).tolist()
    s_af_z = z_af.astype(np.int64).tolist()
    
    s_distances = np.sqrt((x_bef - x_af)**2 + (y_bef - y_af)**2 + (z_bef - z_af)**2).tolist()
    s_x = ((x_bef + x_af)/2).tolist()
    s_y = ((y_bef + y_af)/2).tolist()
    s_z = ((z_bef + z_af)/2).tolist()

    ratios = np.linspace(0.1, 0.9, num=3)  # 9 evenly spaced points between 0.1 and 0.9

    # Generate sampling points for each coordinate
    s_x_t = [r * x_b + (1 - r) * x_a for r in ratios for x_b, x_a in zip(x_bef, x_af)]
    s_y_t = [r * y_b + (1 - r) * y_a for r in ratios for y_b, y_a in zip(y_bef, y_af)]
    s_z_t = [r * z_b + (1 - r) * z_a for r in ratios for z_b, z_a in zip(z_bef, z_af)]

    # s_x_2 = (0.75*x_bef + 0.25*x_af).tolist()
    # s_y_2 = (0.75*y_bef + 0.25*y_af).tolist()
    # s_z_2 = (0.75*z_bef + 0.25*z_af).tolist()

    # s_x_3 = (0.25*x_bef + 0.75*x_af).tolist()
    # s_y_3 = (0.25*y_bef + 0.75*y_af).tolist()
    # s_z_3 = (0.25*z_bef + 0.75*z_af).tolist()

    x_bef, y_bef, z_bef = d_bef_coords_repeated['x'].values, d_bef_coords_repeated['y'].values, d_bef_coords_repeated['z'].values
    x_af, y_af, z_af = d_af_coords_repeated['x'].values, d_af_coords_repeated['y'].values, d_af_coords_repeated['z'].values

    d_bef_x = x_bef.astype(np.int64).tolist()
    d_bef_y = y_bef.astype(np.int64).tolist()
    d_bef_z = z_bef.astype(np.int64).tolist()

    d_af_x = x_af.astype(np.int64).tolist()
    d_af_y = y_af.astype(np.int64).tolist()
    d_af_z = z_af.astype(np.int64).tolist()

    # Calculate distances using vectorized operations
    d_distances = np.sqrt((x_bef - x_af)**2 + (y_bef - y_af)**2 + (z_bef - z_af)**2).tolist()
    d_x = ((x_bef + x_af)/2).tolist()
    d_y = ((y_bef + y_af)/2).tolist()
    d_z = ((z_bef + z_af)/2).tolist()

    # Generate sampling points for each coordinate
    d_x_t = [r * x_b + (1 - r) * x_a for r in ratios for x_b, x_a in zip(x_bef, x_af)]
    d_y_t = [r * y_b + (1 - r) * y_a for r in ratios for y_b, y_a in zip(y_bef, y_af)]
    d_z_t = [r * z_b + (1 - r) * z_a for r in ratios for z_b, z_a in zip(z_bef, z_af)]

    # d_x_2 = (0.75*x_bef + 0.25*x_af).tolist()
    # d_y_2 = (0.75*y_bef + 0.25*y_af).tolist()
    # d_z_2 = (0.75*z_bef + 0.25*z_af).tolist()

    # d_x_3 = (0.25*x_bef + 0.75*x_af).tolist()
    # d_y_3 = (0.25*y_bef + 0.75*y_af).tolist()
    # d_z_3 = (0.25*z_bef + 0.75*z_af).tolist()

    connection_type_n = ["n"] * len(src)
    
    # return src, dst, s_bef, s_bef_x, s_bef_y, s_bef_z, s_af, s_af_x, s_af_y, s_af_z, s_x, s_y, s_z, s_x_2, s_y_2, s_z_2, s_x_3, s_y_3, s_z_3, s_distances, d_bef, d_bef_x, d_bef_y, d_bef_z, d_af, d_af_x, d_af_y, d_af_z, d_x, d_y, d_z, d_x_2, d_y_2, d_z_2, d_x_3, d_y_3, d_z_3, d_distances, connection_type_n, bef_mapping, af_mapping
    return src, dst, s_bef, s_bef_x, s_bef_y, s_bef_z, s_af, s_af_x, s_af_y, s_af_z, s_x, s_y, s_z, s_x_t, s_y_t, s_z_t, s_distances, d_bef, d_bef_x, d_bef_y, d_bef_z, d_af, d_af_x, d_af_y, d_af_z, d_x, d_y, d_z, d_x_t, d_y_t, d_z_t , d_distances, connection_type_n, bef_mapping, af_mapping



In [18]:
def overalll(id_list):
    #ensure no duplicate ids
    id_list= list(set(id_list))

    #to remove neurons that failed loading
    id_list_copy= id_list.copy()

    #all of the columns in the new df
    neurons={}
    src, dst, s_bef, s_bef_x, s_bef_y, s_bef_z, s_af, s_af_x, s_af_y, s_af_z, s_x, s_y, s_z, s_x_2, s_y_2, s_z_2, s_x_3, s_y_3, s_z_3, s_x_t, s_y_t, s_z_t, s_distances, d_bef, d_bef_x, d_bef_y, d_bef_z, d_af, d_af_x, d_af_y, d_af_z, d_x, d_y, d_z, d_x_2, d_y_2, d_z_2, d_x_3, d_y_3, d_z_3, d_x_t, d_y_t, d_z_t, d_distances, connection_type_n, n_id = [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], [], []

    bef_mapping, af_mapping = {}, {}
    i=0
    for id in id_list:
        #load neuron and its connectors
        n= get_neuron_local(id, 3000, 10000)
        # n, c = get_neuron_local(id, 3000, 1000)

        #if loading failed remove from copied list
        if n == None:
             id_list_copy.remove(id)
             continue
        
        #store neuron and connectors information in neuron dict
        neurons[id] = {"n": n}
        # neurons[id] = {"n": n, "c": c}
        edges = n.edges

        ##angst das namen doppelt vergeben werden, fueg noch neuronen id zu namen hinzu
        # src_temp, dst_temp, s_bef_temp, s_bef_x_temp, s_bef_y_temp, s_bef_z_temp, s_af_temp, s_af_x_temp, s_af_y_temp, s_af_z_temp, s_x_temp, s_y_temp, s_z_temp, s_x_2_temp, s_y_2_temp, s_z_2_temp, s_x_3_temp, s_y_3_temp, s_z_3_temp, s_distances_temp, d_bef_temp, d_bef_x_temp, d_bef_y_temp, d_bef_z_temp, d_af_temp, d_af_x_temp, d_af_y_temp, d_af_z_temp, d_x_temp, d_y_temp, d_z_temp, d_x_2_temp, d_y_2_temp, d_z_2_temp, d_x_3_temp, d_y_3_temp, d_z_3_temp, d_distances_temp, connection_type_n_temp, bef_mapping, af_mapping = spatial_connectome_creation(edges, n)
        src_temp, dst_temp, s_bef_temp, s_bef_x_temp, s_bef_y_temp, s_bef_z_temp, s_af_temp, s_af_x_temp, s_af_y_temp, s_af_z_temp, s_x_temp, s_y_temp, s_z_temp, s_x_t_temp, s_y_t_temp, s_z_t_temp, s_distances_temp, d_bef_temp, d_bef_x_temp, d_bef_y_temp, d_bef_z_temp, d_af_temp, d_af_x_temp, d_af_y_temp, d_af_z_temp, d_x_temp, d_y_temp, d_z_temp, d_x_t_temp, d_y_t_temp, d_z_t_temp, d_distances_temp, connection_type_n_temp, bef_mapping, af_mapping = spatial_connectome_creation(edges, n)
        
        # neurons[id].update({"src": src_temp, "dst": dst_temp, "s_x": s_x_temp, "s_y": s_y_temp, "s_z": s_z_temp, "s_x": s_x_temp, "s_y": s_y_temp, "s_z": s_z_temp, "s_x_2": s_x_2_temp, "s_y_2": s_y_2_temp, "s_z_2": s_z_2_temp,"s_x_3": s_x_3_temp, "s_y_3": s_y_3_temp, "s_z_3": s_z_3_temp, "d_x": d_x_temp, "d_y": d_y_temp, "d_z": d_z_temp, "d_x_2": d_x_2_temp, "d_y_2": d_y_2_temp, "d_z_2": d_z_2_temp, "d_x_3": d_x_3_temp, "d_y_3": d_y_3_temp, "d_z_3": d_z_3_temp, "bef_mapping": bef_mapping, "af_mapping": af_mapping})
        neurons[id].update({"src": src_temp, "dst": dst_temp, "s_x": s_x_temp, "s_y": s_y_temp, "s_z": s_z_temp, "s_x": s_x_temp, "s_y": s_y_temp, "s_z": s_z_temp, "s_x_t": s_x_t_temp, "s_y_t": s_y_t_temp, "s_z_t": s_z_t_temp , "d_x": d_x_temp, "d_y": d_y_temp, "d_z": d_z_temp, "d_x_t": d_x_t_temp, "d_y_t": d_y_t_temp, "d_z_t": s_z_t_temp , "bef_mapping": bef_mapping, "af_mapping": af_mapping})
        # print((src_temp))
        src.extend(src_temp)
        dst.extend(dst_temp)
        s_bef.extend(s_bef_temp)
        s_bef_x.extend(s_bef_x_temp)
        s_bef_y.extend(s_bef_y_temp)
        s_bef_z.extend(s_bef_z_temp)
        s_af.extend(s_af_temp)
        s_af_x.extend(s_af_x_temp)
        s_af_y.extend(s_af_y_temp)
        s_af_z.extend(s_af_z_temp)
        s_x.extend(s_x_temp)
        s_y.extend(s_y_temp)
        s_z.extend(s_z_temp)
        s_distances.extend(s_distances_temp)
        d_bef.extend(d_bef_temp)
        d_bef_x.extend(d_bef_x_temp)
        d_bef_y.extend(d_bef_y_temp)
        d_bef_z.extend(d_bef_z_temp)
        d_af.extend(d_af_temp)
        d_af_x.extend(d_af_x_temp)
        d_af_y.extend(d_af_y_temp)
        d_af_z.extend(d_af_z_temp)
        d_x.extend(d_x_temp)
        d_y.extend(d_y_temp)
        d_z.extend(d_z_temp)
        d_distances.extend(d_distances_temp)
        connection_type_n.extend(connection_type_n_temp)
        n_id.extend([id]* len(src_temp))
        print(i)
        i+=1
    
    if id_list_copy == []:
        return None
    
    synaptic_src, synaptic_dst, connection_type_s, x, y, z, n_combo, dists, synaptic_s_bef, synaptic_s_af, synaptic_d_bef, synaptic_d_af= synaptic_data(neurons, id_list_copy)

    spatial_connectome_edge_dict = {
    "src": src + synaptic_src,
    "dst": dst + synaptic_dst,
    "s_bef": s_bef + synaptic_s_bef,
    "s_bef_x": s_bef_x + [0]* len(synaptic_src),
    "s_bef_y": s_bef_y + [0]* len(synaptic_src),
    "s_bef_z": s_bef_z + [0]* len(synaptic_src),
    "s_af": s_af+ synaptic_s_af,
    "s_af_x": s_af_x+ [0]* len(synaptic_src),
    "s_af_y": s_af_y+ [0]* len(synaptic_src),
    "s_af_z": s_af_z+ [0]* len(synaptic_src),
    "s_x": s_x+ x,
    "s_y": s_y+ y,
    "s_z": s_z+ z,
    "s_distance": s_distances+ dists,
    "d_bef": d_bef+ synaptic_d_bef,
    "d_bef_x": d_bef_x+ [0]* len(synaptic_src),
    "d_bef_y": d_bef_y+ [0]* len(synaptic_src),
    "d_bef_z": d_bef_z+ [0]* len(synaptic_src),
    "d_af": d_af+ synaptic_d_af,
    "d_af_x": d_af_x+ [0]* len(synaptic_src),
    "d_af_y": d_af_y+ [0]* len(synaptic_src),
    "d_af_z": d_af_z+ [0]* len(synaptic_src),
    "d_x": d_x+ x,
    "d_y": d_y+ y,
    "d_z": d_z+ z,
    "d_distance": d_distances+ dists,
    "n_id": n_id + n_combo,
    "connection_type": connection_type_n + connection_type_s
    }
    # spatial_connectome_edge_dict = {
    # "src": src ,
    # "dst": dst ,
    # "s_bef": s_bef ,
    # "s_bef_x": s_bef_x ,
    # "s_bef_y": s_bef_y ,
    # "s_bef_z": s_bef_z ,
    # "s_af": s_af,
    # "s_af_x": s_af_x,
    # "s_af_y": s_af_y,
    # "s_af_z": s_af_z,
    # "s_x": s_x,
    # "s_y": s_y,
    # "s_z": s_z,
    # "s_distance": s_distances,
    # "d_bef": d_bef,
    # "d_bef_x": d_bef_x,
    # "d_bef_y": d_bef_y,
    # "d_bef_z": d_bef_z,
    # "d_af": d_af,
    # "d_af_x": d_af_x,
    # "d_af_y": d_af_y,
    # "d_af_z": d_af_z,
    # "d_x": d_x,
    # "d_y": d_y,
    # "d_z": d_z,
    # "d_distance": d_distances,
    # "n_id": n_id ,
    # "connection_type": connection_type_n
    # }
    
    # Step 5: Connect to Arkouda and initialize the graph
    # ak.connect()
    # graph = ar.PropGraph()
    # spatial_connectome_edge_df = ak.DataFrame(spatial_connectome_edge_dict)
    # graph.load_edge_attributes(spatial_connectome_edge_df, source_column="src", destination_column="dst", 
    #                            relationship_columns=["s_bef", "s_bef_x", "s_bef_y", "s_bef_z", "s_af", "s_af_x", 
    #                                                  "s_af_y", "s_af_z", 's_x', "s_y", "s_z", "s_distance", "d_bef",
    #                                                  "d_bef_x", "d_bef_y", "d_bef_z", "d_af", "d_af_x", "d_af_y", "d_af_z",
    #                                                    "d_x", "d_y", "d_z", "d_distance", "n_id", "connection_type"])
    # ak.disconnect()

    # return graph ,spatial_connectome_edge_df, neurons
    return spatial_connectome_edge_dict

In [19]:
d= overalll(root_ids2)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [41]:
df = pd.DataFrame(d)
df.to_csv("/home/michaelshewarega/Desktop/test/OL_random_2.csv", index=False)

In [52]:
df = pd.DataFrame(d)
df

src              dst  s_bef  s_bef_x  s_bef_y  s_bef_z  \
0         328535863013441  285718156140881    821   686728   205070   202355   
1         328535863013441  361349432766191    821   686728   205070   202355   
2         340540827557177  328535863013441    851   687537   204522   202256   
3         340540827557177  357747943403111    851   687537   204522   202256   
4         354946785009842  340540827557177    887   687891   204866   201314   
...                   ...              ...    ...      ...      ...      ...   
1187303   914176572848441   59545684001365   1240        0        0        0   
1187304   914176572848441   59545684001365   1240        0        0        0   
1187305  1123552497597685  174465061404730   1524        0        0        0   
1187306  1094800169903761  167069259889183   1485        0        0        0   
1187307  1220130829083966  197600645634932   1655        0        0        0   

         s_af  s_af_x  s_af_y  s_af_z  ...  d_af  d_af_x  d_af_y  d_af_z  \
0         851  687537  204522  202256  ...   821  686728  205070  202355   
1         851  687537  204522  202256  ...   821  686728  205070  202355   
2         887  687891  204866  201314  ...   851  687537  204522  202256   
3         887  687891  204866  201314  ...   851  687537  204522  202256   
4        1112  689654  202416  197523  ...   887  687891  204866  201314   
...       ...     ...     ...     ...  ...   ...     ...     ...     ...   
1187303  1201       0       0       0  ...   339       0       0       0   
1187304  1201       0       0       0  ...   339       0       0       0   
1187305  1561       0       0       0  ...   450       0       0       0   
1187306  2026       0       0       0  ...   954       0       0       0   
1187307  1561       0       0       0  ...   954       0       0       0   

                d_x            d_y            d_z   d_distance  \
0        685831.375  204207.000000  202226.531250  2504.102783   
1        687333.250  206213.921875  202207.859375  2603.231689   
2        687133.125  204796.640625  202306.062500   982.650818   
3        687799.500  202593.843750  203313.812500  4429.739258   
4        687714.625  204694.546875  201785.578125  1063.493286   
...             ...            ...            ...          ...   
1187303  804268.000  302390.000000  140320.000000     0.000000   
1187304  804502.000  302370.000000  140220.000000     0.000000   
1187305  808272.000  299102.000000  137140.000000     0.000000   
1187306  811012.000  301350.000000  140280.000000     0.000000   
1187307  811054.000  300328.000000  139600.000000     0.000000   

                                          n_id  connection_type  
0                           720575940627202051                n  
1                           720575940627202051                n  
2                           720575940627202051                n  
3                           720575940627202051                n  
4                           720575940627202051                n  
...                                        ...              ...  
1187303  720575940661264001_720575940632390471                s  
1187304  720575940661264001_720575940632390471                s  
1187305  720575940661264001_720575940632390471                s  
1187306  720575940661264001_720575940632390471                s  
1187307  720575940661264001_720575940632390471                s  

[1187308 rows x 28 columns]

In [57]:
df = pd.read_csv("/home/michaelshewarega/Desktop/test/OL_random_2.csv")
df

/tmp/ipykernel_136616/2719178787.py:1: DtypeWarning: Columns (26) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("/home/michaelshewarega/Desktop/test/OL_random_2.csv")


src              dst  s_bef  s_bef_x  s_bef_y  s_bef_z  \
0         328535863013441  285718156140881    821   686728   205070   202355   
1         328535863013441  361349432766191    821   686728   205070   202355   
2         340540827557177  328535863013441    851   687537   204522   202256   
3         340540827557177  357747943403111    851   687537   204522   202256   
4         354946785009842  340540827557177    887   687891   204866   201314   
...                   ...              ...    ...      ...      ...      ...   
1187303   914176572848441   59545684001365   1240        0        0        0   
1187304   914176572848441   59545684001365   1240        0        0        0   
1187305  1123552497597685  174465061404730   1524        0        0        0   
1187306  1094800169903761  167069259889183   1485        0        0        0   
1187307  1220130829083966  197600645634932   1655        0        0        0   

         s_af  s_af_x  s_af_y  s_af_z  ...  d_af  d_af_x  d_af_y  d_af_z  \
0         851  687537  204522  202256  ...   821  686728  205070  202355   
1         851  687537  204522  202256  ...   821  686728  205070  202355   
2         887  687891  204866  201314  ...   851  687537  204522  202256   
3         887  687891  204866  201314  ...   851  687537  204522  202256   
4        1112  689654  202416  197523  ...   887  687891  204866  201314   
...       ...     ...     ...     ...  ...   ...     ...     ...     ...   
1187303  1201       0       0       0  ...   339       0       0       0   
1187304  1201       0       0       0  ...   339       0       0       0   
1187305  1561       0       0       0  ...   450       0       0       0   
1187306  2026       0       0       0  ...   954       0       0       0   
1187307  1561       0       0       0  ...   954       0       0       0   

                d_x            d_y            d_z   d_distance  \
0        685831.375  204207.000000  202226.531250  2504.102783   
1        687333.250  206213.921875  202207.859375  2603.231689   
2        687133.125  204796.640625  202306.062500   982.650818   
3        687799.500  202593.843750  203313.812500  4429.739258   
4        687714.625  204694.546875  201785.578125  1063.493286   
...             ...            ...            ...          ...   
1187303  804268.000  302390.000000  140320.000000     0.000000   
1187304  804502.000  302370.000000  140220.000000     0.000000   
1187305  808272.000  299102.000000  137140.000000     0.000000   
1187306  811012.000  301350.000000  140280.000000     0.000000   
1187307  811054.000  300328.000000  139600.000000     0.000000   

                                          n_id  connection_type  
0                           720575940627202051                n  
1                           720575940627202051                n  
2                           720575940627202051                n  
3                           720575940627202051                n  
4                           720575940627202051                n  
...                                        ...              ...  
1187303  720575940661264001_720575940632390471                s  
1187304  720575940661264001_720575940632390471                s  
1187305  720575940661264001_720575940632390471                s  
1187306  720575940661264001_720575940632390471                s  
1187307  720575940661264001_720575940632390471                s  

[1187308 rows x 28 columns]

In [44]:
df = pd.read_csv("/home/michaelshewarega/Desktop/test/OL_random_2.csv")

/tmp/ipykernel_136616/1010843231.py:1: DtypeWarning: Columns (26) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("/home/michaelshewarega/Desktop/test/OL_random_2.csv")


In [58]:
part_df = df[df["connection_type"] == "n"]
part_df

src              dst  s_bef  s_bef_x  s_bef_y  s_bef_z  \
0       328535863013441  285718156140881    821   686728   205070   202355   
1       328535863013441  361349432766191    821   686728   205070   202355   
2       340540827557177  328535863013441    851   687537   204522   202256   
3       340540827557177  357747943403111    851   687537   204522   202256   
4       354946785009842  340540827557177    887   687891   204866   201314   
...                 ...              ...    ...      ...      ...      ...   
654773  613694744806897  654123425885547   1943   802723   362615   180172   
654774  644332104686784  721083428921532   2040   803378   358070   182149   
654775  644332104686784  734033240829416   2040   803378   358070   182149   
654776  654123425885547  660124558233231   2071   804317   363279   179092   
654777  654123425885547  679391351559595   2071   804317   363279   179092   

        s_af  s_af_x  s_af_y  s_af_z  ...  d_af  d_af_x  d_af_y  d_af_z  \
0        851  687537  204522  202256  ...   821  686728  205070  202355   
1        851  687537  204522  202256  ...   821  686728  205070  202355   
2        887  687891  204866  201314  ...   851  687537  204522  202256   
3        887  687891  204866  201314  ...   851  687537  204522  202256   
4       1112  689654  202416  197523  ...   887  687891  204866  201314   
...      ...     ...     ...     ...  ...   ...     ...     ...     ...   
654773  1565  799484  360176  182773  ...  1943  802723  362615  180172   
654774  1824  801148  360058  184671  ...  2040  803378  358070  182149   
654775  1824  801148  360058  184671  ...  2040  803378  358070  182149   
654776  1943  802723  362615  180172  ...  2071  804317  363279  179092   
654777  1943  802723  362615  180172  ...  2071  804317  363279  179092   

                d_x            d_y            d_z   d_distance  \
0       685831.3750  204207.000000  202226.531250  2504.102783   
1       687333.2500  206213.921875  202207.859375  2603.231689   
2       687133.1250  204796.640625  202306.062500   982.650818   
3       687799.5000  202593.843750  203313.812500  4429.739258   
4       687714.6250  204694.546875  201785.578125  1063.493286   
...             ...            ...            ...          ...   
654773  803520.3125  362947.875000  179632.218750  2037.182373   
654774  805301.0000  358991.625000  181468.718750  4474.605469   
654775  806191.4375  358822.687500  181892.765625  5845.084961   
654776  804241.6250  362987.656250  177539.000000  3164.269531   
654777  804748.1250  363950.875000  177192.046875  4120.965332   

                      n_id  connection_type  
0       720575940627202051                n  
1       720575940627202051                n  
2       720575940627202051                n  
3       720575940627202051                n  
4       720575940627202051                n  
...                    ...              ...  
654773  720575940614717438                n  
654774  720575940614717438                n  
654775  720575940614717438                n  
654776  720575940614717438                n  
654777  720575940614717438                n  

[654778 rows x 28 columns]

In [59]:
src_t = part_df[["src", "n_id"]].drop_duplicates().values
dst_t = part_df[["dst", "n_id"]].drop_duplicates().values
# Merging src_t and dst_t using numpy.vstack
merged = np.vstack((src_t, dst_t))

# Remove duplicates by converting to a DataFrame and using drop_duplicates
merged_df = pd.DataFrame(merged, columns=["value", "n_id"]).drop_duplicates()

# Extract the first value of every element (i.e., the "value" column)
first_values = merged_df["value"].tolist()

# Compare the total length with the length of unique values
total_length = len(first_values)
unique_length = len(set(first_values))

print(f"Total length: {total_length}")
print(f"Unique values length: {unique_length}")

Total length: 667682
Unique values length: 667676


In [18]:
df = pd.DataFrame(d)
df.to_csv("/home/michaelshewarega/Desktop/test/OL_5000_2.csv", index=False)

In [151]:
neurons[root_ids[0]]['n'].nodes

node_id label            x             y              z  radius    type  \
0         1     1  804313.1250  284848.81250   67841.140625   145.0    root   
1         3     5  819933.0000  304209.59375  222003.390625   172.0     end   
2        43     6  797561.0000  288139.15625   88226.585938   220.0     end   
3       113     5  798487.5625  290710.15625   88514.031250   676.0  branch   
4       421     5  802583.2500  288837.00000   66374.695312   267.0     end   
5       443     5  802652.0625  286995.93750   67686.234375   400.0  branch   
6       445     6  802704.5625  298499.56250   98143.734375     0.0     end   
7       583     6  804913.0625  300377.75000  101943.226562   105.0     end   
8       587     5  805050.4375  298556.75000   99784.476562   669.0  branch   
9       665     5  806366.5625  299179.25000  102397.554688   836.0  branch   
10      834     5  819175.1875  308743.59375  222483.937500  1314.0     end   
11      911     5  821901.8125  305905.65625  221700.046875  1613.0  branch   
12     1283     5  840243.6875  312361.15625  214327.734375   739.0     end   
13     1387     5  842526.8750  309948.28125  215609.046875   685.0     end   
14     1431     5  843621.9375  308187.00000  212611.109375  1905.0  branch   
15     1445     5  843679.8125  307942.40625  213654.750000  1728.0  branch   
16     1500     6  844935.2500  307907.53125  212177.046875    77.0     end   
17     1514     5  845303.7500  309627.34375  211420.687500  1052.0  branch   

    parent_id  
0          -1  
1         911  
2         113  
3         443  
4         443  
5           1  
6         587  
7         665  
8         113  
9         587  
10        911  
11       1431  
12       1514  
13       1445  
14       1514  
15       1431  
16       1445  
17        665

In [147]:
import pickle

with open('/home/michaelshewarega/Desktop/test/neurons_dict.pkl', 'wb') as file:
    pickle.dump(neurons, file)

In [2]:
# df = pd.DataFrame(d)
# df.to_csv("/home/michaelshewarega/Desktop/test/final_output.csv", index=False)
df_downloaded = pd.read_csv("/home/michaelshewarega/Desktop/test/final_output.csv")
# df_downloaded_ak = ak.DataFrame(df_downloaded.to_dict(orient='list'))
df_downloaded

/tmp/ipykernel_638180/2070561768.py:3: DtypeWarning: Columns (26) have mixed types. Specify dtype option on import or set low_memory=False.
  df_downloaded = pd.read_csv("/home/michaelshewarega/Desktop/test/final_output.csv")


src       dst  s_bef  s_bef_x  s_bef_y  s_bef_z  s_af  s_af_x  \
0           280121     70028     28   738022   325844   117401   121  746473   
1           280121    220028     28   738022   325844   117401   121  746473   
2          1210141    280121    121   746473   329771   108835   141  748561   
3          1210141   1200121    121   746473   329771   108835   141  748561   
4          1410165   1210141    141   748561   330100   108720   165  749695   
...            ...       ...    ...      ...      ...      ...   ...     ...   
10289882    110049   3030458     11        0        0        0    49       0   
10289883  13231302  21952518   1323        0        0        0  1302       0   
10289884  13231302  21952518   1323        0        0        0  1302       0   
10289885  23922400  36063391   2392        0        0        0  2400       0   
10289886  26553063  40774075   2655        0        0        0  3063       0   

          s_af_y  s_af_z  ...  d_af  d_af_x  d_af_y  d_af_z          d_x  \
0         329771  108835  ...    28  738022  325844  117401  737538.1875   
1         329771  108835  ...    28  738022  325844  117401  737917.0000   
2         330100  108720  ...   121  746473  329771  108835  742248.1250   
3         330100  108720  ...   121  746473  329771  108835  746802.1250   
4         330126  107343  ...   141  748561  330100  108720  747517.5625   
...          ...     ...  ...   ...     ...     ...     ...          ...   
10289882       0       0  ...   458       0       0       0  699034.0000   
10289883       0       0  ...  2518       0       0       0  789760.0000   
10289884       0       0  ...  2518       0       0       0  790272.0000   
10289885       0       0  ...  3391       0       0       0  802620.0000   
10289886       0       0  ...  4075       0       0       0  809700.0000   

                 d_y            d_z    d_distance  \
0         325047.000  117041.421875   1999.659302   
1         326053.875  117641.187500    671.531616   
2         327807.875  113118.312500  12657.466797   
3         329754.375  109198.750000    979.928955   
4         329936.125  108777.859375   2116.711426   
...              ...            ...           ...   
10289882  250214.000  175520.000000   1571.915429   
10289883  276970.000  146500.000000   2044.114298   
10289884  276228.000  146540.000000   1204.049226   
10289885  275132.000  137020.000000   2394.249760   
10289886  276338.000  128000.000000    537.732764   

                                           n_id  connection_type  
0                            720575940627005443                n  
1                            720575940627005443                n  
2                            720575940627005443                n  
3                            720575940627005443                n  
4                            720575940627005443                n  
...                                         ...              ...  
10289882  720575940661316481_720575940641428365                s  
10289883  720575940661316481_720575940641428365                s  
10289884  720575940661316481_720575940641428365                s  
10289885  720575940661316481_720575940641428365                s  
10289886  720575940661316481_720575940641428365                s  

[10289887 rows x 28 columns]